In [1]:
import pandas as pd
import seaborn as sns
import time
import re
import nltk
import math
import os
from Bio.SeqUtils.ProtParam import ProteinAnalysis
from sklearn import svm
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer

In [2]:
def fasta_parser(filename):
    if os.path.exists(filename):
        pass
    else:                     
        print("The file, %s, does not exist" % filename)
        
    file = open(filename,mode='r')
    rec_all = file.read()
    file.close()
    # remove all whitespace from string all_of_it
    rec_all = rec_all.replace(' ','')
    # split records by > 
    records = rec_all.split('>')
    # Parse out the headers & sequences for each record
    headers = []
    sequences = []
    for rec in records:
        s = ''
        data = rec.split('\n')
        sq = s.join(data[1:])
        if len(data[0]) > 0:
            headers.append(data[0])
   
        if (len(sq) > 0):
            sequences.append(s.join(data[1:]))
    
    return headers, sequences

In [3]:
import glob
glob.glob('*.fasta')

['uniprot-ER-136K.fasta', 'uniprot-ER_reviewed.fasta']

In [4]:
# concatenate all relevant fasta files into one fasta file use glob
# see https://stackoverflow.com/questions/17749058/combine-multiple-text-files-into-one-text-file-using-python/17749339
# Note the code below works with no bizzare artifacts from globbing or concatenation
#read_files = glob.glob("*.fasta")

#with open("isomerase_2000.fasta", "wb") as outfile:
    #for f in read_files:
        #with open(f, "rb") as infile:
            #outfile.write(infile.read())

In [5]:
#er_head, er_seqs = fasta_parser('uniprot-ER_reviewed.fasta')
f_name = 'uniprot-ER-136K.fasta'
er_head, er_seqs = fasta_parser(f_name)

In [6]:
for hd in er_head[0:3]:
    print(hd)
    print()

sp|P30040|ERP29_HUMANEndoplasmicreticulumresidentprotein29OS=HomosapiensOX=9606GN=ERP29PE=1SV=4

sp|P16615|AT2A2_HUMANSarcoplasmic/endoplasmicreticulumcalciumATPase2OS=HomosapiensOX=9606GN=ATP2A2PE=1SV=1

sp|Q64578|AT2A1_RATSarcoplasmic/endoplasmicreticulumcalciumATPase1OS=RattusnorvegicusOX=10116GN=Atp2a1PE=1SV=1



In [7]:
for sq in er_seqs[0:3]:
    print(sq)
    print()

MAAAVPRAAFLSPLLPLLLGFLLLSAPHGGSGLHTKGALPLDTVTFYKVIPKSKFVLVKFDTQYPYGEKQDEFKRLAENSASSDDLLVAEVGISDYGDKLNMELSEKYKLDKESYPVFYLFRDGDFENPVPYTGAVKVGAIQRWLKGQGVYLGMPGCLPVYDALAGEFIRASGVEARQALLKQGQDNLSSVKETQKKWAEQYLKIMGKILDQGEDFPASEMTRIARLIEKNKMSDGKKEELQKSLNILTAFQKKGAEKEEL

MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEGKTLLELVIEQFEDLLVRILLLAACISFVLAWFEEGEETITAFVEPFVILLILVANAIVGVWQERNAENAIEALKEYEPEMGKVYRQDRKSVQRIKAKDIVPGDIVEIAVGDKVPADIRLTSIKSTTLRVDQSILTGESVSVIKHTDPVPDPRAVNQDKKNMLFSGTNIAAGKAMGVVVATGVNTEIGKIRDEMVATEQERTPLQQKLDEFGEQLSKVISLICIAVWIINIGHFNDPVHGGSWIRGAIYYFKIAVALAVAAIPEGLPAVITTCLALGTRRMAKKNAIVRSLPSVETLGCTSVICSDKTGTLTTNQMSVCRMFILDRVEGDTCSLNEFTITGSTYAPIGEVHKDDKPVNCHQYDGLVELATICALCNDSALDYNEAKGVYEKVGEATETALTCLVEKMNVFDTELKGLSKIERANACNSVIKQLMKKEFTLEFSRDRKSMSVYCTPNKPSRTSMSKMFVKGAPEGVIDRCTHIRVGSTKVPMTSGVKQKIMSVIREWGSGSDTLRCLALATHDNPLRREEMHLEDSANFIKYETNLTFVGCVGMLDPPRIEVASSVKLCRQAGIRVIMITGDNKGTAVAICRRIGIFGQDEDVTSKAFTGREFDELNPSAQRDACLNARCFARVEPSHKSKIVEFLQSFDEITAMTGDGVNDAPALKKAEIGIAMGSGTAVAKTASEMVLADD

In [8]:
print(len(er_seqs))

136191


In [9]:
er_seqs2 = list(set(er_seqs))
print(len(er_seqs2))

124423


In [10]:
from Bio import SeqIO
records = list(SeqIO.parse(f_name, "fasta"))

In [11]:
seq_ids =[]
seqs = []
#for record in SeqIO.parse("isomerase_2000.fasta", "fasta"):
for record in SeqIO.parse(f_name, "fasta"):
    #print(repr(record.seq))
    #print()
    seq_ids.append(record.id)
    seqs.append(str(record.seq))

In [12]:
print(len(seq_ids))
print()
print(len(seqs))

136191

136191


In [13]:
seqs[0:3]

['MAAAVPRAAFLSPLLPLLLGFLLLSAPHGGSGLHTKGALPLDTVTFYKVIPKSKFVLVKFDTQYPYGEKQDEFKRLAENSASSDDLLVAEVGISDYGDKLNMELSEKYKLDKESYPVFYLFRDGDFENPVPYTGAVKVGAIQRWLKGQGVYLGMPGCLPVYDALAGEFIRASGVEARQALLKQGQDNLSSVKETQKKWAEQYLKIMGKILDQGEDFPASEMTRIARLIEKNKMSDGKKEELQKSLNILTAFQKKGAEKEEL',
 'MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEGKTLLELVIEQFEDLLVRILLLAACISFVLAWFEEGEETITAFVEPFVILLILVANAIVGVWQERNAENAIEALKEYEPEMGKVYRQDRKSVQRIKAKDIVPGDIVEIAVGDKVPADIRLTSIKSTTLRVDQSILTGESVSVIKHTDPVPDPRAVNQDKKNMLFSGTNIAAGKAMGVVVATGVNTEIGKIRDEMVATEQERTPLQQKLDEFGEQLSKVISLICIAVWIINIGHFNDPVHGGSWIRGAIYYFKIAVALAVAAIPEGLPAVITTCLALGTRRMAKKNAIVRSLPSVETLGCTSVICSDKTGTLTTNQMSVCRMFILDRVEGDTCSLNEFTITGSTYAPIGEVHKDDKPVNCHQYDGLVELATICALCNDSALDYNEAKGVYEKVGEATETALTCLVEKMNVFDTELKGLSKIERANACNSVIKQLMKKEFTLEFSRDRKSMSVYCTPNKPSRTSMSKMFVKGAPEGVIDRCTHIRVGSTKVPMTSGVKQKIMSVIREWGSGSDTLRCLALATHDNPLRREEMHLEDSANFIKYETNLTFVGCVGMLDPPRIEVASSVKLCRQAGIRVIMITGDNKGTAVAICRRIGIFGQDEDVTSKAFTGREFDELNPSAQRDACLNARCFARVEPSHKSKIVEFLQSFDEITAMTGDGVNDAPALKKAEIGIAMGSGTAVAKTASEM

In [14]:
#print(len(records))

In [15]:
seqID = []
for item in records:
    seqID.append(item.id)
    print(item.id)
    print()

sp|P30040|ERP29_HUMAN

sp|P16615|AT2A2_HUMAN

sp|Q64578|AT2A1_RAT

sp|Q8R429|AT2A1_MOUSE

sp|O55143|AT2A2_MOUSE

sp|P04191|AT2A1_RABIT

sp|P11507|AT2A2_RAT

sp|O14983|AT2A1_HUMAN

sp|P11607|AT2A2_PIG

sp|Q0VCY0|AT2A1_BOVIN

sp|P70083|AT2A1_MAKNI

sp|P13585|AT2A1_CHICK

sp|Q9DC23|DJC10_MOUSE

sp|Q8R180|ERO1A_MOUSE

sp|P52555|ERP29_RAT

sp|Q86YB8|ERO1B_HUMAN

sp|Q92105|AT2A1_PELES

sp|Q8R4A1|ERO1A_RAT

sp|P11598|PDIA3_RAT

sp|P22700|ATC1_DROME

sp|P30101|PDIA3_HUMAN

sp|P38659|PDIA4_RAT

sp|Q8R2E9|ERO1B_MOUSE

sp|P27773|PDIA3_MOUSE

sp|O95881|TXD12_HUMAN

sp|P13667|PDIA4_HUMAN

tr|Q9CVM7|Q9CVM7_MOUSE

tr|H0VH33|H0VH33_CAVPO

tr|A0A3L7HTH1|A0A3L7HTH1_CRIGR

tr|A0A5E4B3V4|A0A5E4B3V4_MARMO

tr|A0A5E4AQS1|A0A5E4AQS1_MARMO

tr|A0A5E4AQ01|A0A5E4AQ01_MARMO

tr|A0A0R4J1F2|A0A0R4J1F2_MOUSE

tr|A0A1A6GRI7|A0A1A6GRI7_NEOLE

tr|A0A1A6GE32|A0A1A6GE32_NEOLE

tr|A0A0N8ET84|A0A0N8ET84_HETGA

tr|A0A1A6GC79|A0A1A6GC79_NEOLE

tr|A0A1A6GPW5|A0A1A6GPW5_NEOLE

tr|A0A0N8ESM3|A0A0N8ESM3_HETGA

tr|G5BGT6|G5BGT6_

tr|A0A091E4Y1|A0A091E4Y1_FUKDA

tr|E0CZB5|E0CZB5_MOUSE

tr|A0A091DTZ7|A0A091DTZ7_FUKDA

tr|A0A0G2K590|A0A0G2K590_RAT

tr|A0A091D2V7|A0A091D2V7_FUKDA

tr|A0A091D0C4|A0A091D0C4_FUKDA

tr|A0A1S3FTD5|A0A1S3FTD5_DIPOR

tr|A0A1S3FHW7|A0A1S3FHW7_DIPOR

tr|A0A1S3EYH0|A0A1S3EYH0_DIPOR

tr|Q9WVT5|Q9WVT5_RAT

tr|B2GUU3|B2GUU3_RAT

tr|A0A250YK98|A0A250YK98_CASCN

tr|A0A1U7Q5Z3|A0A1U7Q5Z3_MESAU

tr|A0A1U7Q9F5|A0A1U7Q9F5_MESAU

tr|A0A1U8BMQ2|A0A1U8BMQ2_MESAU

tr|I3LW52|I3LW52_ICTTR

tr|A0A3Q0DE75|A0A3Q0DE75_MESAU

tr|A0A1U7Q8H4|A0A1U7Q8H4_MESAU

tr|A0A1S3F6G3|A0A1S3F6G3_DIPOR

tr|A0A1S3ENL3|A0A1S3ENL3_DIPOR

tr|A0A091CNF1|A0A091CNF1_FUKDA

tr|A0A1S3GCM9|A0A1S3GCM9_DIPOR

tr|A0A1S3FS43|A0A1S3FS43_DIPOR

tr|A0A3L7GLR1|A0A3L7GLR1_CRIGR

tr|A0A3L7H6X0|A0A3L7H6X0_CRIGR

tr|A0A3L7I2V5|A0A3L7I2V5_CRIGR

tr|A0A3L7HDS9|A0A3L7HDS9_CRIGR

tr|H0WCY0|H0WCY0_CAVPO

tr|A0A286XAN9|A0A286XAN9_CAVPO

tr|A0A1U7Q608|A0A1U7Q608_MESAU

tr|A0A250YGV4|A0A250YGV4_CASCN

tr|E0CZ10|E0CZ10_MOUSE

tr|B9EHY2|B9EHY2_MOUSE

tr|A0A

tr|B0E9S5|B0E9S5_ENTDS

tr|A0A2K8FTM3|A0A2K8FTM3_NILLU

tr|E2AQ19|E2AQ19_CAMFO

tr|A0A0A1X7T9|A0A0A1X7T9_ZEUCU

tr|B4JPZ4|B4JPZ4_DROGR

tr|A0A1I9WL46|A0A1I9WL46_NILLU

tr|A0A086QJ91|A0A086QJ91_TOXGO

tr|A0A0C2M8D4|A0A0C2M8D4_THEKT

tr|A0A3P7GSV1|A0A3P7GSV1_HYDTA

tr|A0A310S4W4|A0A310S4W4_9HYME

tr|A0A3P6QQ26|A0A3P6QQ26_CYLGO

tr|A0A0J9SX05|A0A0J9SX05_PLAVI

tr|A0A086PGW9|A0A086PGW9_TOXGO

tr|A0A0V1NS09|A0A0V1NS09_9BILA

tr|S9UN52|S9UN52_9TRYP

tr|E9AQ79|E9AQ79_LEIMU

tr|A0A2A9MA47|A0A2A9MA47_9APIC

tr|A0A2L0CN53|A0A2L0CN53_9COLE

tr|A0A0D6LUQ1|A0A0D6LUQ1_9BILA

tr|A0A2A2KI08|A0A2A2KI08_9BILA

tr|A0A177B1Y0|A0A177B1Y0_9METZ

tr|A0A2A2LQC9|A0A2A2LQC9_9BILA

tr|Q8IKF2|Q8IKF2_PLAF7

tr|A0A1L8EG16|A0A1L8EG16_HAEIR

tr|A0A1S0UHH2|A0A1S0UHH2_LOALO

tr|A4ZIT2|A4ZIT2_9DIPT

tr|F1KZR1|F1KZR1_ASCSU

tr|F1L878|F1L878_ASCSU

tr|W6L1P9|W6L1P9_9TRYP

tr|A0A1I8CQC0|A0A1I8CQC0_9BILA

tr|S4PT52|S4PT52_9NEOP

tr|S4P9Y5|S4P9Y5_9NEOP

tr|A0A2M3YYK4|A0A2M3YYK4_9DIPT

tr|A8WP54|A8WP54_CAEBR

tr|A0A164LT80|A0


tr|A0A443SLE5|A0A443SLE5_9ACAR

tr|A0A443SET6|A0A443SET6_9ACAR

tr|A0A182VRF2|A0A182VRF2_9DIPT

tr|A0A1L8EAZ1|A0A1L8EAZ1_HAEIR

tr|A0A182W406|A0A182W406_9DIPT

tr|A0A1S0UG28|A0A1S0UG28_LOALO

tr|A0A1S0UJQ8|A0A1S0UJQ8_LOALO

tr|A0A1C6XDE2|A0A1C6XDE2_PLACH

tr|A0A1I7VFE0|A0A1I7VFE0_LOALO

tr|A0A1D1W986|A0A1D1W986_RAMVA

tr|F1KXA8|F1KXA8_ASCSU

tr|A0A0L7KBP3|A0A0L7KBP3_PLAFX

tr|A0A1B6H6D3|A0A1B6H6D3_9HEMI

tr|A0A1B6D306|A0A1B6D306_9HEMI

tr|A0A1J4MMN4|A0A1J4MMN4_9CRYT

tr|A0A4U5NF45|A0A4U5NF45_STECR

tr|A0A1B0AAR3|A0A1B0AAR3_GLOPL

tr|A0A1J4MCV8|A0A1J4MCV8_9CRYT

tr|A0A1L8ED63|A0A1L8ED63_HAEIR

tr|G0R2U8|G0R2U8_ICHMG

tr|Q8IDZ5|Q8IDZ5_PLAF7

tr|A0A4V6A061|A0A4V6A061_STECR

tr|A0A4D5R9D2|A0A4D5R9D2_SCOVI

tr|O97275|O97275_PLAF7

tr|A0A509ANT8|A0A509ANT8_PLABA

tr|W2SN57|W2SN57_NECAM

tr|A0A1I7W0J3|A0A1I7W0J3_LOALO

tr|A0A2S2R469|A0A2S2R469_9HEMI

tr|W2TKA1|W2TKA1_NECAM

tr|A0A0R3RSB1|A0A0R3RSB1_9BILA

tr|C3Z7Y3|C3Z7Y3_BRAFL

tr|A0A2P8XQU3|A0A2P8XQU3_BLAGE

tr|A0A016VXE2|A0A016VXE2_9BILA


tr|A0A1Y2GH84|A0A1Y2GH84_9FUNG

tr|A0A1Y2H2V0|A0A1Y2H2V0_9FUNG

tr|A0A4V4JXA1|A0A4V4JXA1_AURPU

tr|A0A4S9KBB6|A0A4S9KBB6_AURPU

tr|A0A4S8VQK8|A0A4S8VQK8_AURPU

tr|A0A319CJP2|A0A319CJP2_ASPVC

tr|A0A4S8UR61|A0A4S8UR61_AURPU

tr|A0A4S8VQR0|A0A4S8VQR0_AURPU

tr|A0A4V4JHU0|A0A4V4JHU0_AURPU

tr|A0A4S9L363|A0A4S9L363_AURPU

tr|A0A4S9X557|A0A4S9X557_AURPU

tr|A0A4S9FH91|A0A4S9FH91_AURPU

tr|A0A319B678|A0A319B678_ASPVC

tr|A6R365|A6R365_AJECN

tr|A0A4S8S9Q2|A0A4S8S9Q2_AURPU

tr|F2TTE5|F2TTE5_AJEDA

tr|A0A2H3F4U5|A0A2H3F4U5_9HELO

tr|A0A2H3F943|A0A2H3F943_9HELO

tr|K2RJV7|K2RJV7_MACPH

tr|A0A3D8RVI0|A0A3D8RVI0_9HELO

tr|A0A084B1Z5|A0A084B1Z5_STACB

tr|R8BUB9|R8BUB9_TOGMI

tr|A0A2H3EY43|A0A2H3EY43_9HELO

tr|A0A2H3ESB6|A0A2H3ESB6_9HELO

tr|A0A1Y2VLW1|A0A1Y2VLW1_9PEZI

tr|A0A2H3FPB8|A0A2H3FPB8_9HELO

tr|A0A1Y2US94|A0A1Y2US94_9PEZI

tr|A0A077QZL2|A0A077QZL2_9BASI

tr|A0A084B9K8|A0A084B9K8_STACB

tr|A0A2H3ETG3|A0A2H3ETG3_9HELO

tr|A0A3D8RVJ1|A0A3D8RVJ1_9HELO

tr|A0A3D8S2P8|A0A3D8S2P8_9HELO

tr|A0A2V

...

sp|Q9GLD9|UDB33_MACMU

sp|P36514|UD2C1_RABIT

sp|Q5PNZ1|ZDH21_ARATH

sp|Q5ZMG1|UFL1_CHICK

sp|Q27979|RDH5_BOVIN

sp|Q8IZV5|RDH10_HUMAN

sp|Q8BGH4|REEP1_MOUSE

sp|Q6NUK4|REEP3_HUMAN

sp|Q4QQW1|REEP4_RAT

sp|O13016|PTN1_CHICK

sp|B5FXJ6|TPC2L_TAEGU

sp|Q0WW17|RWA2_ARATH

sp|Q5R9P3|SC23A_PONAB

sp|Q9M291|SC24C_ARATH

sp|O08547|SC22B_MOUSE

sp|O94979|SC31A_HUMAN

sp|Q39208|SC5D1_ARATH

sp|Q752H7|SC61A_ASHGO

sp|O43043|SCAP_SCHPO

sp|Q5XHH7|SYVNB_XENLA

sp|P36371|TAP2_MOUSE

sp|Q6P1M0|S27A4_HUMAN

sp|Q6T707|SCD4_MOUSE

sp|Q8C7E7|STBD1_MOUSE

sp|Q6CU99|SMP3_KLULA

sp|E2RG47|STT3B_CANLF

sp|P38435|VKGC_HUMAN

sp|Q86AQ7|VAM7B_DICDI

sp|Q54NL4|VMP1_DICDI

sp|O94296|YOOC_SCHPO

sp|P70496|PLD1_RAT

sp|Q41142|PLDA1_RICCO

sp|Q9GMB0|RPN1_PIG

sp|P91390|RPN2_CAEEL

sp|Q4R4X6|RAB2A_MACFA

sp|Q99P75|RAB9A_RAT

sp|P61356|RL27_BOVIN

sp|P50170|RDH16_RAT

sp|Q9QYF1|RDH11_MOUSE

sp|Q9AST3|SBH2_ARATH

sp|Q05AS9|SC23A_XENTR

sp|Q9CQR2|RS21_MOUSE

sp|P58681|TLR7_MOUSE

sp|P62268|RS23_RAT

sp|Q2TA63|TM147_RAT


sp|Q96K19|RN170_HUMAN

sp|Q8CBG9|RN170_MOUSE

sp|Q6FKL3|ROT1_CANGA

sp|A5DN48|ROT1_PICGU

sp|Q5AY94|ROT1_EMENI

sp|Q9YI25|RPE65_AMBTI

sp|Q6AXT5|RAB21_RAT

sp|Q6C6S3|RFT1_YARLI

sp|Q5A6N8|RFT1_CANAL

sp|Q2NKY9|JAGN1_BOVIN

sp|Q17667|LNP1_CAEEL

sp|O94414|LNP_SCHPO

sp|Q8BLY7|HPS6_MOUSE

sp|P92958|KIN11_ARATH

sp|A3LXZ3|MKAR_PICST

sp|Q5A368|NTE1_CANAL

sp|A5JSS2|RL21_CAPHI

sp|P61358|RL27_MOUSE

sp|Q03530|RCE1_YEAST

sp|Q14257|RCN2_HUMAN

sp|O93434|RCN1_TAKRU

sp|Q8BH97|RCN3_MOUSE

sp|I6L9G5|RCN3_RAT

sp|A1L1W4|RD10A_DANRE

sp|O02853|PTGDS_BOVIN

sp|P41222|PTGDS_HUMAN

sp|Q9TUI1|PTGDS_MACFU

sp|O09114|PTGDS_MOUSE

sp|Q29095|PTGDS_PIG

sp|Q8WNM0|PTGDS_PONPY

sp|Q29626|PTGIS_BOVIN

sp|Q14571|ITPR2_HUMAN

sp|Q91V01|MBOA5_MOUSE

sp|A5PK45|GT251_BOVIN

sp|P24389|IOD1_RAT

sp|A1CFK8|PATA_ASPCL

sp|A0A075TMP8|PATI_PENEN

sp|Q53LQ0|PDI11_ORYSJ

sp|Q765A7|PGAP1_RAT

sp|A7YWP2|PGAP3_BOVIN

sp|Q28661|PROC_RABIT

sp|Q9JI85|NUCB2_RAT

sp|P04070|PROC_HUMAN

sp|Q75T13|PGAP1_HUMAN

sp|Q68KI4|NHX1_ARA


sp|Q7ZTW4|SGK1_DANRE

sp|Q710E6|SUCO_RAT

sp|Q8VD00|SGMR2_MOUSE

sp|Q5ZL84|SGMR1_CHICK

sp|Q96HN2|SAHH3_HUMAN

sp|Q6CRH4|SHE3_KLULA

sp|Q9TSM6|TP4A1_MACFA

sp|A5E5G3|SAR1_LODEL

sp|P0C951|SAR1_ASPNC

sp|Q22169|SSRB_CAEEL

sp|Q877B9|SAR1_ASPOR

sp|P0CT17|SAR1_MAGOY

sp|Q9CQC9|SAR1B_MOUSE

sp|Q6FWD3|SC242_CANGA

sp|Q870W0|SC61A_NEUCR

sp|Q9JJZ4|UB2J1_MOUSE

sp|Q9UTA3|YL8H_SCHPO

sp|Q6P7B7|ZFY27_RAT

sp|Q3EC77|PMT5_ARATH

sp|Q38882|PLDA1_ARATH

sp|A0A0R4IVV0|MTP_DANRE

sp|O60568|PLOD3_HUMAN

sp|Q5R6K5|PLOD3_PONAB

sp|Q6CFU5|ROT1_YARLI

sp|P55745|RAB21_CANLF

sp|B2GV22|PTSS2_RAT

sp|Q5R9J9|TPPC4_PONAB

sp|B0FWK4|SPCS1_PIG

sp|P36057|SRPB_YEAST

sp|Q612Q9|RS21_CAEBR

sp|B4GSC0|RS21_DROPE

sp|P63221|RS21_PIG

sp|Q9CY27|TECR_MOUSE

sp|Q962Q7|RS23_SPOFR

sp|Q9BVC6|TM109_HUMAN

sp|Q9GRJ3|RS23_LUMRU

sp|P62267|RS23_MOUSE

sp|Q9NT68|TEN2_HUMAN

sp|P56984|TM14A_PIG

sp|Q8R1K1|UBAC2_MOUSE

sp|Q6FQK7|UBC6_CANGA

sp|Q9P6J9|YHD1_SCHPO

sp|Q8T191|UGGG_DICDI

sp|Q8WV99|ZFN2B_HUMAN

sp|Q04311|VMS1_YEAST

sp|P35016|ENPL_CATRO

sp|Q6ZNL6|FGD5_HUMAN

sp|P08110|ENPL_CHICK

sp|Q86IX2|DOPP1_DICDI

sp|Q58CR4|DOLK_BOVIN

sp|A5GFZ5|DPM1_PIG

sp|Q68ES4|ER21B_XENLA

sp|Q5RFP3|ERAP2_PONAB

sp|Q12959|DLG1_HUMAN

sp|P18413|ERD2_KLULA

sp|Q7S4Z3|GPI14_NEUCR

sp|Q74ZS2|GPI13_ASHGO

sp|Q6FSS4|ERFB_CANGA

sp|Q92206|ERG1_CANAL

sp|Q06551|ERFB_YEAST

sp|O13306|ERG1_CANGA

sp|Q28J34|ERLN2_XENTR

sp|Q99393|IZH4_YEAST

sp|Q0VCY6|MBOA7_BOVIN

sp|Q8IYU2|HACE1_HUMAN

sp|Q9D3B1|HACD2_MOUSE

sp|Q28BK1|HACE1_XENTR

sp|Q0P4Y8|LMF2_XENTR

sp|Q9LDF2|LAG11_ARATH

sp|Q9Y4K0|LOXL2_HUMAN

sp|Q9DCZ4|MIC26_MOUSE

sp|Q60664|LRMP_MOUSE

sp|Q643R3|LPCT4_HUMAN

sp|Q12912|LRMP_HUMAN

sp|Q8K1F9|LCTL_MOUSE

sp|Q9W0H3|LDAH_DROME

sp|Q10479|ALG8_SCHPO

sp|Q5AJD2|ALG8_CANAL

sp|P43571|BST1_YEAST

sp|Q641Y1|C56D2_RAT

sp|Q0IIZ2|ASNA_XENTR

sp|P11090|CRUA_BRANA

sp|A6QPT7|ERAP2_BOVIN

sp|O42580|ERD23_XENLA

sp|P18414|ERD2_YEAST

sp|Q6BZ57|GPI7_DEBHA

sp|G5EEQ9|ERG28_CAEEL

sp|Q3SZM3|CYBC1_BOVIN

sp|P35176|CYPD_YEAST

sp|Q7T2D4|ERGI2_D

sp|P24390|ERD21_HUMAN

sp|Q2U9J2|GPI7_ASPOR

sp|P49018|GPI8_YEAST

sp|Q76NM1|ERD2_PLAF7

sp|Q8TGB2|GPI7_CANAL

sp|Q6FVF9|ERFD_CANGA

sp|Q59QL0|ERFB_CANAL

sp|Q5HZS2|CYBC1_XENLA

sp|O76062|ERG24_HUMAN

sp|Q4R5C3|ERGI2_MACFA

sp|Q5EAE0|ERGI3_BOVIN

sp|Q5RCJ9|ERLN1_PONAB

sp|Q9D1Q6|ERP44_MOUSE

sp|Q9C7S7|ERO1_ARATH

sp|Q9Z2E3|ERN2_MOUSE

sp|P08050|CXA1_RAT

sp|Q54GC1|DGAT2_DICDI

sp|Q6S9C0|CXA1_CANLF

sp|Q4JK73|DHB11_MACFA

sp|Q8VCH6|DHC24_MOUSE

sp|P0CS02|GMT1_CRYNJ

sp|Q5RE51|DEGS1_PONAB

sp|Q9ZTP3|EIN4_ARATH

sp|Q9NZJ5|E2AK3_HUMAN

sp|Q6C3M9|GET3_YARLI

sp|C6HRP6|GET3_AJECH

sp|Q9Y753|FDFT_YARLI

sp|A8N0V8|GET3_COPC7

sp|E1BPW0|ENTP5_BOVIN

sp|E1C1L6|ENTP5_CHICK

sp|Q99JX3|GORS2_MOUSE

sp|Q5FVL3|DIK1B_RAT

sp|P23818|GRIA1_MOUSE

sp|Q5NDL1|EOGT_PANTR

sp|Q9VQB7|EOGT_DROME

sp|D5JBW8|GAO_CICIN

sp|X2JI34|GAO_TANPA

sp|Q3V3G7|GRM2A_MOUSE

sp|Q9P2K9|DISP3_HUMAN

sp|O43292|GPAA1_HUMAN

sp|O94633|DPM3_SCHPO

sp|Q10MW6|DJC27_ORYSJ

sp|Q7XVN7|DJC43_ORYSJ

sp|P81999|DJB11_CANLF

sp|Q59VN0|GPI18

## Create pandas dataframe using seqID & sequences

In [16]:
# create dataframe of 2000 additional isomerase sequences
#d_iso = {'name':seq_ids,'sequence':seqs}
d_er = {'name':seqID,'sequence':er_seqs}
df = pd.DataFrame(d_er)
df.head()

name                                           sequence
0  sp|P30040|ERP29_HUMAN  MAAAVPRAAFLSPLLPLLLGFLLLSAPHGGSGLHTKGALPLDTVTF...
1  sp|P16615|AT2A2_HUMAN  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...
2    sp|Q64578|AT2A1_RAT  MEAAHSKSTEECLSYFGVSETTGLTPDQVKRHLEKYGPNELPAEEG...
3  sp|Q8R429|AT2A1_MOUSE  MEAAHSKSTEECLSYFGVSETTGLTPDQVKRHLEKYGPNELPAEEG...
4  sp|O55143|AT2A2_MOUSE  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...

In [17]:
d_er2 = {'name':seq_ids,'sequence':seqs}

df2 = pd.DataFrame(d_er2)
df2.head()

name                                           sequence
0  sp|P30040|ERP29_HUMAN  MAAAVPRAAFLSPLLPLLLGFLLLSAPHGGSGLHTKGALPLDTVTF...
1  sp|P16615|AT2A2_HUMAN  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...
2    sp|Q64578|AT2A1_RAT  MEAAHSKSTEECLSYFGVSETTGLTPDQVKRHLEKYGPNELPAEEG...
3  sp|Q8R429|AT2A1_MOUSE  MEAAHSKSTEECLSYFGVSETTGLTPDQVKRHLEKYGPNELPAEEG...
4  sp|O55143|AT2A2_MOUSE  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...

In [18]:
df.shape

(136191, 2)

In [19]:
df2.shape

(136191, 2)

In [20]:
# remove non-coding amino acid letters like X,B,U
df['sequence'] = df['sequence'].str.replace('U','G')
df['sequence'] = df['sequence'].str.replace('X','G')
df['sequence'] = df['sequence'].str.replace('B','G')

In [21]:
# remove non-coding amino acid letters like X,B,U
df2['sequence'] = df2['sequence'].str.replace('U','G')
df2['sequence'] = df2['sequence'].str.replace('X','G')
df2['sequence'] = df2['sequence'].str.replace('B','G')

In [22]:
#df['MW'] = df['sequence'].apply(lambda seq: ProteinAnalysis(seq).molecular_weight())
#df.head()

In [23]:
#df2['MW'] = df2['sequence'].apply(lambda seq: ProteinAnalysis(seq).molecular_weight())
#df2.head()

In [24]:
# Create 2 columns for the dataframe
df['location'] = 0
df['label'] = 'ER'

df.head(10)

name                                           sequence  \
0  sp|P30040|ERP29_HUMAN  MAAAVPRAAFLSPLLPLLLGFLLLSAPHGGSGLHTKGALPLDTVTF...   
1  sp|P16615|AT2A2_HUMAN  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...   
2    sp|Q64578|AT2A1_RAT  MEAAHSKSTEECLSYFGVSETTGLTPDQVKRHLEKYGPNELPAEEG...   
3  sp|Q8R429|AT2A1_MOUSE  MEAAHSKSTEECLSYFGVSETTGLTPDQVKRHLEKYGPNELPAEEG...   
4  sp|O55143|AT2A2_MOUSE  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...   
5  sp|P04191|AT2A1_RABIT  MEAAHSKSTEECLAYFGVSETTGLTPDQVKRHLEKYGHNELPAEEG...   
6    sp|P11507|AT2A2_RAT  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...   
7  sp|O14983|AT2A1_HUMAN  MEAAHAKTTEECLAYFGVSETTGLTPDQVKRNLEKYGLNELPAEEG...   
8    sp|P11607|AT2A2_PIG  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...   
9  sp|Q0VCY0|AT2A1_BOVIN  MEAAHSKTTEECLAYFGVSETTGLTPDQVKRHLEKYGHNELPAEEG...   

   location label  
0         0    ER  
1         0    ER  
2         0    ER  
3         0    ER  
4         0    ER  
5         0    ER  
6         0    ER  
7         0    ER  
8         0    ER  
9         0    ER

In [25]:
df.shape

(136191, 4)

In [26]:
# remove the duplicate protein sequences
df = df.drop_duplicates(subset='sequence', keep="first")
df.shape

(124421, 4)

In [27]:
df.head(10)

name                                           sequence  \
0  sp|P30040|ERP29_HUMAN  MAAAVPRAAFLSPLLPLLLGFLLLSAPHGGSGLHTKGALPLDTVTF...   
1  sp|P16615|AT2A2_HUMAN  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...   
2    sp|Q64578|AT2A1_RAT  MEAAHSKSTEECLSYFGVSETTGLTPDQVKRHLEKYGPNELPAEEG...   
3  sp|Q8R429|AT2A1_MOUSE  MEAAHSKSTEECLSYFGVSETTGLTPDQVKRHLEKYGPNELPAEEG...   
4  sp|O55143|AT2A2_MOUSE  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...   
5  sp|P04191|AT2A1_RABIT  MEAAHSKSTEECLAYFGVSETTGLTPDQVKRHLEKYGHNELPAEEG...   
6    sp|P11507|AT2A2_RAT  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...   
7  sp|O14983|AT2A1_HUMAN  MEAAHAKTTEECLAYFGVSETTGLTPDQVKRNLEKYGLNELPAEEG...   
8    sp|P11607|AT2A2_PIG  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...   
9  sp|Q0VCY0|AT2A1_BOVIN  MEAAHSKTTEECLAYFGVSETTGLTPDQVKRHLEKYGHNELPAEEG...   

   location label  
0         0    ER  
1         0    ER  
2         0    ER  
3         0    ER  
4         0    ER  
5         0    ER  
6         0    ER  
7         0    ER  
8         0    ER  
9         0    ER

## Save dataframe of ER sequences as a csv file

In [ ]:
#df.to_csv('uniprot-ER-reviewed.csv',index = None)

#proteins = pd.read_csv('uniprot-ER-reviewed.csv')

#proteins.head()

In [28]:
df.to_csv('uniprot-ER-136K.csv',index = None)

proteins = pd.read_csv('uniprot-ER-136K.csv')

proteins.head()

name                                           sequence  \
0  sp|P30040|ERP29_HUMAN  MAAAVPRAAFLSPLLPLLLGFLLLSAPHGGSGLHTKGALPLDTVTF...   
1  sp|P16615|AT2A2_HUMAN  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...   
2    sp|Q64578|AT2A1_RAT  MEAAHSKSTEECLSYFGVSETTGLTPDQVKRHLEKYGPNELPAEEG...   
3  sp|Q8R429|AT2A1_MOUSE  MEAAHSKSTEECLSYFGVSETTGLTPDQVKRHLEKYGPNELPAEEG...   
4  sp|O55143|AT2A2_MOUSE  MENAHTKTVEEVLGHFGVNESTGLSLEQVKKLKERWGSNELPAEEG...   

   location label  
0         0    ER  
1         0    ER  
2         0    ER  
3         0    ER  
4         0    ER